<table style="width: 100%; border-style: none">
<tr style="border-style: none; background-color: #82a8cf">
<td style="border-style: none; width: 1%; text-align: left; font-size: 18px; color: #ffffff">Institut f&uuml;r Theoretische Physik<br /> <font color="#e6e6e6">Universit&auml;t zu K&ouml;ln </font></td>
<td style="border-style: none; width: 1%; font-size: 16px">&nbsp;</td>
<td style="border-style: none; width: 1%; text-align: right; font-size: 18px; color: #ffffff">Prof. Dr. Simon Trebst<br /> <font color="#e6e6e6"> Theo Haas </font> </td>
</tr>
</table>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h1 style="font-weight:200; text-align: center; margin: 0px; font-size: 48px; padding:0px; color: #606060">Computer-Physik </h1>
<h1 style="font-weight:light; text-align: center; margin: 10px; padding:0px; color: #606060"> Schöner Plotten mit Makie &mdash; Teil 2 </h1>
<hr  style="height: 2px; border-color: #606060; background-color: #606060"> 
<h3 style="font-weight:400; text-align: center; margin: 0px; font-size: 20px; padding:0px; margin-bottom: 20px; color: #606060">Sommersemester 2025</h3>
<!--<h3 style="font-weight:bold; text-align: center; margin: 0px; font-size: 15px; padding:0px; margin-bottom: 20px;">Website: <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2023-CompPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2023-CompPhys.shtml</a></h3> -->

<font size="4" color="#606060">**Website:** <a href="https://www.thp.uni-koeln.de/trebst/Lectures/2025-CompPhys.shtml" style="color:#82a8cf; text-decoration: underline;text-decoration-style: dotted;">https://www.thp.uni-koeln.de/trebst/Lectures/2025-CompPhys.shtml</a></font>

<font size="4" color="#606060">**Themen dieses Notebooks**: <span style="color:#606060"> CairoMakie and GLMakie, Observable, einfache Animationen, interaktive Blockelemente, Events, weiterführende Links  </span> 
    
<hr style="height:.3px"> 

# 1. CairoMakie vs. GLMakie
Was bisher geschah...

In [ ]:
using CairoMakie

In [ ]:
fig = Figure(size = (600,400))
ax = Axis(fig[1,1])
lines!(ax, 0:0.01:3pi, cos)

fig # Anzeigen der Figure im Notebook

Für interaktive Plots benutzen wir das Paket GLMakie (eigentlich nur ein anderes Backend, alle Plot-Funktionen, die wir bisher kennengelernt haben, bleiben gleich).

In [ ]:
using GLMakie

In [ ]:
fig = Figure(size = (600,400))
ax = Axis(fig[1,1])
lines!(ax, 0:0.01:3pi, cos)

display(fig) # Anzeigen der Figure im Notebook

# Zoomen mit Mausrad / Scrollen
# Ctrl + Links --> zurueck auf Anfangsachsen
# Rechte Maustaste --> verschieben.

Wenn beide Pakete geladen sind kann man mit `CairoMakie.activate!()` und `GLMakie.activate!()` zwischen beiden hin- und herwechseln.

In [ ]:
CairoMakie.activate!()
fig, ax, p = scatter(rand(10))

# 2. Observables
Der Datentyp `Observable` steht in Makie hinter allem Animierten und Interaktiven.

In [ ]:
a = 1 
typeof(a)

In [ ]:
aO = Observable(1)

In [ ]:
typeof(aO)

In [ ]:
b = [1,2,3,4]

In [ ]:
bO = Observable(b)

In [ ]:
typeof(bO)

Wie greift man auf den Wert der Observablen zu und wie kann man den ändern?

In [ ]:
bval = bO[]

In [ ]:
bval = to_value(bO)

In [ ]:
bval[1] = 10

In [ ]:
bO[]

In [ ]:
bO[] = 2.

In [ ]:
bO[][3] = 67
bO

In [ ]:
bO[] = [1,2,3,4,5,6,7,8,9]
bO

### Wofür sind `Observable`s nützlich?

In [ ]:
GLMakie.activate!()
fig = Figure(size = (400,800))

ax1 = Axis(fig[1,1])
ax2 = Axis(fig[2,1])

a = rand(10)
aO = Observable(a)

scatterlines!(ax1, a)
scatterlines!(ax2, aO)

display(fig)

In [ ]:
a = 0.5 * ones(10);

In [ ]:
aO[] = 0.1 * collect(1:10)

#### Wenn man den Wert einer Observablen ändert (mittels `O[] = ...`), aktualisiert sich der Plot, der die Observable enthält automatisch.
Damit können wir schon eine erste Mini-Animation schreiben. Dafür brauchen wir denn Befehl `sleep()` der eine Pause mit der Länge des übergebenen Arguments einfügt.

In [ ]:
sleep(4)

In [ ]:
fig = Figure()
ax = Axis(fig[1,1])

x = range(0, 2pi, 200)
y = Observable(sin.(x))

lines!(ax, x, y, linewidth = 4)

display(fig)

In [ ]:
sleep(4)
for i in 0:0.01:2pi
    
    y[] = sin.(x .+ i)
    sleep(0.01) 
end

Allgemeiner kann man Observable an Funktionen oder Programmstücke binden, die ausgeführt werden, wenn sich der Wert der Observablen ändert.

In [ ]:
x = Observable(1)

In [ ]:
on(x) do x
    # Hier kann ich jetzt Sachen mit x (Wert der Observablen) machen.
    println("New value of x is $x")
end

In [ ]:
x[] = 2

In [ ]:
y = Observable(20)
on(println, y)

In [ ]:
y[] = 1

In [ ]:
function f(x)
    println("Das doppelte des Wertes der Observablen ist ", 2*x)
    scatterlines!(ax3, rand(10))
end

In [ ]:
on(f, y)

In [ ]:
y[] = 5

In [ ]:
fig = Figure()
ax3 = Axis(fig[1,1])

display(fig)

In [ ]:
y[] = 12

### Verknüpfen von Observablen.
Das wird zum Beispiel wichtig, wenn man später mit interaktiven Elementen (Slider, etc.) arbeitet. Ziel: Eine Observable definieren, die sich immer ändert, wenn sich der Wert einer anderen Observablen ändert. Das kann man mit der Funktion `lift` erreichen. Auch bei komplexen Animationen ist es praktisch, wenn man nur eine einzelne Observable ändern muss, und diese alle Änderungen weitergibt.

In [ ]:
a = Observable(5.)

In [ ]:
f(x) = x^2
b = lift(f , a)

In [ ]:
a[] = 9

In [ ]:
b

Alternative Syntax:

In [ ]:
c = lift(a) do a
    # Hier kann man jetzt alles mögliche machen, am Ende hat die
    # Observable c den Wert, der in der letzten Zeile steht
    # Dabei kann man auf den Wert der Observablen a mit a zugreifen.
    x1 = a^2 * ones(10) .+ 1
    return x1 / 2  
end

In [ ]:
a[] = 4

In [ ]:
b[]

In [ ]:
c

Beispiel mit Plotten einer Funktion:

In [ ]:
fig = Figure()
ax = Axis(fig[1,1])

x = Observable(1)

y = lift(x) do x
    return sin.(x * range(0,2pi,400))
end 

scatterlines!(ax, y, linewidth = 4)

display(fig)

In [ ]:
x[] = 10

# 3. Interaktive Blocks

Wir hatten im ersten Tutorium bereits verschiedene Block-Elemente kennengelernt, z.B. `Legend`, `Axis`, etc. Daneben gibt es auch noch eine Reihe von Blocks, die zur Interaktion wichtig sind, z.B. Schaltflächen (`Button`), Auswahlmenüs (`Menu`) oder Regler (`Slider`). Diese können also genau so positioniert werden und besitzen einige der gleichen Optionen, wie die bereits bekannten Blocks.

In [ ]:
fig = Figure()

# Menu
menu = Menu(fig[1, 1:2], options = ["A", "B", "C"])

# Slider
slider = Slider(fig[2, 1])

# Toggle
toggle = Toggle(fig[2, 2], tellheight = false)

# Button
button = Button(fig[3, 1], label = "Hier klicken", tellwidth = :false)

display(fig)

Wie immer gilt: `?` ist nützlich für Informationen über die spezifischen Optionen und die Anwendung.

In [ ]:
?Slider

### Slider

In [ ]:
fig = Figure()

slider = Slider(fig[1, 1], range = range(-10, 10, step = 0.1),
    startvalue = 0.5)
Label(fig[1, 2], map(v ->  "m = $v", slider.value), width = 80)

display(fig)

In [ ]:
typeof(slider.value)

Der Wert des Sliders ist also eine Observable. Wir können diese Observable also an eine weitere, in einem Plot dargestellte Observable knüpfen (mittels `lift`) und damit den Plot durch Betätigen des Sliders live verändern.

In [ ]:
fig = Figure()
ax = Axis(fig[1,1:2])

slider = Slider(fig[2, 1], range = range(-10, 10, step = 0.1),
    startvalue = 0.5)
Label(fig[2, 2], map(v ->  "m = $v", slider.value), width = 80)

xs = range(0,10, length = 100)
ys = lift(slider.value) do sv
    return cos.(xs) + sv * ones(100)
end


scatterlines!(ax, xs, ys)

xlims!(ax, 0, 10)
ylims!(ax, -11, 11)

display(fig)

Man kann den Sliders natürlich auch anders benutzen. Ein Beispiel findet sich in der Aufgabe zum gekickten Rotor. Dort wurde der Wert des Sliders einfach als Parameter in einer Funktion benutzt, die an die Observable "Klicken der Maus" gebunden war. Hier noch ein Beispiel:

In [ ]:
fig = Figure()
ax = Axis(fig[1,1:2])

slider = Slider(fig[2, 1], range = range(-1, 1, step = 0.1), startvalue = 0.)
Label(fig[2, 2], map(v ->  "m = $v", slider.value), width = 80)

# Jedes Mal, wenn sich der Slider-Wert ändert, soll das hier passieren.
on(slider.value) do sl
    scatterlines!(ax, 0:10, sl * (0:10))
end

scatterlines!(ax, 0:10, zeros(11))
xlims!(ax, 0, 10)
ylims!(ax, -11, 11)

display(fig)

### Button

In [ ]:
fig = Figure()

meinbutton   = Button(fig[1, 1], label = "Hier klicken!")

display(fig)

In [ ]:
typeof(meinbutton.clicks)

Es gibt also eine Observable, die Klick-Events registriert. Wieder können wir z.B. `on` benutzen, um Interaktivität hinzuzufügen.

In [ ]:
fig = Figure()
ax = Axis(fig[1,1])
limits!(ax, 0,1,0,1.05)

meinbutton = Button(fig[2, 1], label = "Hier klicken!", tellwidth = false)

on(meinbutton.clicks) do _
    scatterlines!(ax, 0.05:0.1:0.95, rand(10))
end 

display(fig)

In [ ]:
fig = Figure()
ax = Axis(fig[1,1])
limits!(ax, 0,1,0,1.05)

meinbutton = Button(fig[2, 1], label = "Hier klicken!", tellwidth = false)


exponent = Observable(0.)
on(meinbutton.clicks) do _ 
    exponent[] += 0.2
end 

ys = lift(exponent) do z
   return (0:0.01:1) .^ z 
end


scatterlines!(ax, 0:0.01:1, ys)

display(fig)

In [ ]:
fig = Figure()
ax = Axis(fig[1,1])

x = Observable(0.)
y = lift(x) do x    
        sin.(range(0,2pi,200) .+ x)
end
 
meinbutton   = Button(fig[2, 1], label = "Go!", tellwidth = false)

on(meinbutton.clicks) do _
    @async for i in 1:100
        x[] = i/20
        sleep(0.1)
    end
end

lines!(ax, range(0,2pi,200) , y, linewidth = 4)

display(fig)

## Ein Beispiel zum dran herumprobieren
inklusive `Slider`, `Menu`, `Button`s und `Toggle`.

In [ ]:
fig = Figure()

f(x) = cos(x) * cos(x)

# Menu zur Auswahl einer Funktion
menu = Menu(fig[1, 1:2], options = [("Sinus", sin), ("Cosinus", cos), (L"\cos^2(x)", f)])

# Slider mit Label zum Auswählen eines Offsets
slider = Slider(fig[2, 1], range = range(-pi, pi, length=101))
Label(fig[2, 2], map(value -> string(round(value * 180 / pi)) * '°', slider.value), width = 80)

# Toggle um scatter plot sichtbar zu machen
toggle = Toggle(fig[3, 2], tellheight = false)

# Buttons um Linienbreite zu ändern
size_up_button   = Button(fig[4, 2], label = "125%", tellheight = false)
size_down_button = Button(fig[5, 2], label = "80%", tellheight = false)
color_button = Button(fig[6, 2], label = "Farbe", tellheight = false)


# Axis, plot & Interaktion
ax = Axis(fig[3:6, 1])
xs = range(0, 2pi, length=101)

# Menu & Slider Interaktion
ys = map(menu.selection, slider.value) do f, shift
    return f.(xs .+ shift)
end

# Button Interaktion
linewidth = Observable(2.0)
on(_ -> linewidth[] = 1.25 * linewidth[], size_up_button.clicks)
on(_ -> linewidth[] = 0.8 * linewidth[], size_down_button.clicks)

mycolors = [:red, :blue, :orange, :green, :black]
c = Observable(1)
d = Observable(:red)
on(color_button.clicks) do _
    c[] = mod(c[] + 1, 5) + 1
    d[] = mycolors[c[]]
end

lines!(ax, xs, ys, linewidth = linewidth, color = d)
scatter!(ax, xs, ys, color = :orange, visible = toggle.active)

display(fig)

# 4. Events

In [ ]:
fig = Figure()
ax = Axis(fig[1,1])
limits!(ax, 0,1,0,1)

display(fig)

In [ ]:
typeof(events(fig).mousebutton)

Es gibt also auch eine Observable, die bei Aktionen mit der Maus ausgelöst wird.

In [ ]:
fig = Figure()
ax = Axis(fig[1,1])
limits!(ax, 0,1,0,1)

m = Observable(0.)

on(events(fig).mousebutton) do event
    
    if event.action == Mouse.press
        coord = mouseposition(ax)
        scatter!(ax, coord)
    
        ax.backgroundcolor = rand([:lightblue, :lightpink, :lightyellow, :lightgreen])
    end
    
    
    if event.button == Mouse.right && event.action == Mouse.press
        m[] += 0.5
        lines!(ax, 0:0.01:1, x->x^m[])
    end
        
end



display(fig)

Analog gibt es auch `events.keyboardbutton`

In [ ]:
typeof(events(fig).keyboardbutton)

# Weiterführende Informationen:
- [Observablen](https://docs.makie.org/stable/documentation/nodes/)
- [Events](https://docs.makie.org/stable/documentation/events/)
- Alle interaktiven [Block-Elemente](https://docs.makie.org/stable/examples/plotting_functions/)

Eine gute Idee ist es auch, die Aufgaben 8 und 9 von Blatt 4 noch einmal durchzuarbeiten und zu probieren, die dort zur Verfügung gestellten Programmskelette zu verstehen.